In [1]:
import pandas as pd
import numpy as np

df_emails=pd.read_csv('./datasets/emails.csv')
df_emails['sentences'] = df_emails['text'].str.split('\n')
df_emails['sentences']=df_emails['sentences'].apply(lambda x: [i.split('\t') for i in x if len(i)>0])
df_emails['sentences']=df_emails['sentences'].apply(lambda x:' '.join(map(' '.join,x)))
df_emails['sentences']=df_emails['sentences'].apply(lambda x:x.replace('\ufeff',''))

In [6]:
df_emails['sentences'].iloc[0]

'ممنون آقا سامان. من پارسال اصلا آزاد شرکت نکرده بودم و سراسری هم قبول نشدم. فقط میخواستم بدونم شرایط چطوریه واسه سال بعد. مرسی از راهنمایی هاتون.'

In [2]:
from hazm import Normalizer, word_tokenize, stopwords_list, Stemmer
normalizer = Normalizer()
stemmer = Stemmer()
def preprocess_text(text):
    # Normalize text
    text = normalizer.normalize(text)
    
    # Tokenize text
    tokens = word_tokenize(text)
    return tokens

# Apply preprocessing to each email in the dataset
df_emails['cleaned_text'] = df_emails['sentences'].apply(preprocess_text)

In [7]:
df_emails['cleaned_text'] 
df_emails.to_csv('cleaned_text_emails.csv',index=False)

In [21]:
df_emails.drop('pos_tagger_emails',axis=1,inplace=True)

In [22]:
df_emails.head()

text label  \
0  ﻿ممنون آقا سامان.\nمن پارسال اصلا آزاد شرکت نک...   ham   
1  ﻿سلام آقای کریمی\nبالاخره آزمونارشد تموم شد من...   ham   
2  ﻿درود بر حاج وحیدی بنده بعنوان یک دکتری تاریخ ...   ham   
3  ﻿با سلام  و احترام\nضمن تقدیر از مسولین محترم ...   ham   
4  ﻿با سلام اینجانب یک دستگاه خودرو پراید 131 با ...   ham   

                                           sentences  \
0  ممنون آقا سامان. من پارسال اصلا آزاد شرکت نکرد...   
1  سلام آقای کریمی بالاخره آزمونارشد تموم شد من ر...   
2  درود بر حاج وحیدی بنده بعنوان یک دکتری تاریخ ک...   
3  با سلام  و احترام ضمن تقدیر از مسولین محترم سا...   
4  با سلام اینجانب یک دستگاه خودرو پراید 131 با ش...   

                                        cleaned_text  
0  [ممنون, آقا, سامان, ., من, پارسال, اصلا, آزاد,...  
1  [سلام, آقای, کریمی, بالاخره, آزمونارشد, تموم, ...  
2  [درود, بر, حاج, وحیدی, بنده, بعنوان, یک, دکتری...  
3  [با, سلام, و, احترام, ضمن, تقدیر, از, مسولین, ...  
4  [با, سلام, اینجانب, یک, دستگاه, خودرو, پراید, ...

In [26]:
import numpy as np
import nltk
import re
import string
import warnings
import gensim
from sklearn.metrics.pairwise import cosine_similarity
from configparser import ConfigParser
from functools import reduce
from gensim.models import Doc2Vec
from hazm import *
model_path = './pos_tagger.model'
tagger = POSTagger(model = model_path)
df_emails['pos_tagger_emails']=df_emails['cleaned_text']
df_emails['pos_tagger_emails']=df_emails['pos_tagger_emails'].apply(lambda x:tagger.tag_sents([x]))
df_emails.to_csv('pos_tagger_emails.csv',index=False)

In [27]:
df_emails['pos_tagger_emails'].head()

0    [[(ممنون, NOUN), (آقا, NOUN), (سامان, NOUN), (...
1    [[(سلام, NOUN,EZ), (آقای, NOUN,EZ), (کریمی, NO...
2    [[(درود, NOUN), (بر, ADP), (حاج, NOUN), (وحیدی...
3    [[(با, ADP), (سلام, NOUN), (و, CCONJ), (احترام...
4    [[(با, ADP), (سلام, NOUN,EZ), (اینجانب, NOUN),...
Name: pos_tagger_emails, dtype: object

In [29]:
keyword_count = 10
grammers = [
"""
NP:
        {<NOUN,EZ>?<NOUN.*>}    # Noun(s) + Noun(optional)

""",

"""
NP:
        {<NOUN.*><ADJ.*>?}    # Noun(s) + Adjective(optional)

"""
]
## you can also add your own grammer to be extracted from the text...
def extract_candidates(tagged, grammer):
    keyphrase_candidate = set()
    np_parser = nltk.RegexpParser(grammer)
    trees = np_parser.parse_sents(tagged)
    for tree in trees:
        for subtree in tree.subtrees(filter=lambda t: t.label() == 'NP'):  # For each nounphrase
            # Concatenate the token with a space
            keyphrase_candidate.add(' '.join(word for word, tag in subtree.leaves()))
    keyphrase_candidate = {kp for kp in keyphrase_candidate if len(kp.split()) <= 5}
    keyphrase_candidate = list(keyphrase_candidate)
    return keyphrase_candidate
def extract_candidates_email(tokens):
    all_candidates = set()
    for grammer in grammers:
        all_candidates.update(extract_candidates(tokens, grammer))


    return np.array(list(all_candidates))
df_emails['candidates_extracted_emails'] = df_emails['pos_tagger_emails'].apply(lambda x:extract_candidates_email(x))

df_emails.to_csv('candidates_extracted_emails.csv',index=False)

[[('ممنون', 'NOUN'), ('آقا', 'NOUN'), ('سامان', 'NOUN'), ('.', 'PUNCT'), ('من', 'PRON'), ('پارسال', 'ADV'), ('اصلا', 'ADV'), ('آزاد', 'ADJ,EZ'), ('شرکت', 'NOUN'), ('نکرده_بودم', 'VERB'), ('و', 'CCONJ'), ('سراسری', 'ADJ'), ('هم', 'CCONJ'), ('قبول', 'ADJ'), ('نشدم', 'VERB'), ('.', 'PUNCT'), ('فقط', 'ADV'), ('می\u200cخواستم', 'VERB'), ('بدونم', 'VERB'), ('شرایط', 'NOUN,EZ'), ('چطوریه', 'ADV'), ('واسه', 'ADP'), ('سال', 'NOUN,EZ'), ('بعد', 'ADV'), ('.', 'PUNCT'), ('مرسی', 'NOUN'), ('از', 'ADP'), ('راهنمایی', 'NOUN,EZ'), ('هاتون', 'NOUN'), ('.', 'PUNCT')]]
[[('سلام', 'NOUN,EZ'), ('آقای', 'NOUN,EZ'), ('کریمی', 'NOUN'), ('بالاخره', 'ADV'), ('آزمونارشد', 'NOUN'), ('تموم', 'ADJ'), ('شد', 'VERB'), ('من', 'PRON'), ('راحت', 'ADJ'), ('شدم', 'VERB'), ('یکم', 'NUM'), ('راهنمایی', 'NOUN'), ('می\u200cخوام', 'VERB'), ('بهترین', 'ADJ'), ('مجله\u200cی', 'NOUN,EZ'), ('تخصصی', 'ADJ,EZ'), ('زبان\u200cشناسی', 'NOUN'), ('که', 'SCONJ'), ('بتونم', 'VERB'), ('اشتراک', 'NOUN'), ('بگیرم', 'VERB'), ('کدومه', 'NOUN'),

In [40]:
df_emails['candidates_extracted_emails'].iloc[0].shape

(10,)

In [34]:
sent2vec_model_path = './sent2vec-naab.model'
sent2vec_model = SentEmbedding(sent2vec_model_path)

In [41]:
def cos_sim_find_emails(email_candidates):
    all_candidates_vectors = [sent2vec_model[candidate] for candidate in email_candidates]
    candidates_concatinate = ' '.join(email_candidates)
    whole_text_vector = sent2vec_model[candidates_concatinate]
    candidates_sim_whole = cosine_similarity(all_candidates_vectors, whole_text_vector.reshape(1,-1))
    candidates_sim_whole_norm = candidates_sim_whole / np.max(candidates_sim_whole)
    candidates_sim_whole_norm = 0.5 + (candidates_sim_whole_norm - np.average(candidates_sim_whole_norm)) / np.std(candidates_sim_whole_norm)
    return candidates_sim_whole_norm
df_emails['cos_sim_norm_emails'] = df_emails['candidates_extracted_emails'].apply(lambda x:cos_sim_find_emails(x))
df_emails.to_csv('cos_sim_norm_extracted_emails.csv',index=False)

In [74]:
df_emails['cos_sim_norm_emails'].iloc[0]

array([[-0.13998944],
       [ 0.8299003 ],
       [ 1.078146  ],
       [ 0.2904632 ],
       [-0.55771196],
       [ 2.615105  ],
       [-0.52219534],
       [ 1.1142356 ],
       [ 1.1047282 ],
       [-0.8126819 ]], dtype=float32)

In [75]:
df_cos_sim_norm_emails = pd.read_csv('cos_sim_norm_extracted_emails.csv')
aa=[1,2,3,4,5]
aa[0:4]
aa=np.pad(aa, (0, keyword_count-len(aa)), 'constant', constant_values=(0))
aa
def choose_the_best_cos_sim(cos_list):
    sorted_cos_list = np.sort(cos_list)
    return sorted_cos_list[0]
k= choose_the_best_cos_sim(df_emails['cos_sim_norm_emails'].iloc[0])
k

array([-0.13998944], dtype=float32)

In [215]:
from itertools import chain
df_cos_sim_norm_emails = pd.read_csv('cos_sim_norm_extracted_emails.csv')
def choose_the_best_cos_sim(cos_list):
    sorted_cos_list = np.sort(cos_list,axis=0)[::-1]
    sorted_cos_list = [item for sublist in sorted_cos_list for item in sublist]
    if len(sorted_cos_list) < keyword_count:
        sorted_cos_list = [sorted_cos_list,np.zeros(keyword_count-len(sorted_cos_list))]
        sorted_cos_list = [item for sublist in sorted_cos_list for item in sublist]
        print(sorted_cos_list)
    return sorted_cos_list[0:keyword_count]
df_emails[str(keyword_count)+'th_cos_sim'] = df_emails['cos_sim_norm_emails'].apply(lambda x:choose_the_best_cos_sim(x))
df_cos_sim_norm_emails.to_csv('10th_cos_sim_extracted_emails.csv',index=False)

[1.7167801, 1.6491361, 1.1621931, 0.46867087, 0.012155563, -0.3219872, -1.1869487, 0.0, 0.0, 0.0]
[1.9999247, 1.1308303, 0.79582024, 0.69542325, 0.61220586, 0.60006666, -0.14660597, -1.6876647, 0.0, 0.0]
[1.7173153, 1.6039499, 1.2066205, 0.6614783, 0.21566373, 0.11358327, 0.06900135, -1.5876124, 0.0, 0.0]
[1.8113664, 1.7831237, 1.617781, 0.701057, 0.33512437, 0.22069716, -0.26726818, -0.8447583, -0.8571234, 0.0]
[2.4202542, 1.0592171, 0.8922062, 0.56815624, 0.43314937, 0.30150044, -0.50472987, -1.1697533, 0.0, 0.0]
[1.499883, 1.4569609, 1.3848226, 1.1446785, 0.7685609, 0.5314933, 0.06804529, -1.1706036, -1.183841, 0.0]
[2.724463, 0.9881401, 0.35528326, 0.07633743, 0.0075252056, -0.26938564, -0.38236344, 0.0, 0.0, 0.0]
[1.402724, 1.318248, 1.224552, 0.63430107, -0.22211128, -1.3577142, 0.0, 0.0, 0.0, 0.0]
[2.0897074, 1.3777326, 1.0569732, 0.98062176, 0.58543783, 0.319997, 0.26988018, -1.0152378, -1.1651118, 0.0]


In [115]:
from sklearn.preprocessing import LabelEncoder
df_emails['label_id'] = LabelEncoder().fit_transform(df_emails['label'])
df_emails.sample(10)

text label  \
623  ﻿\nشامل 5000 كتاب الكترونيكي فارسي در زمينه ها...  spam   
519  ﻿    فیلترینگ بدن انسان\n\n\n*پد دفع سموم بدن ...  spam   
404  ﻿سلام. خیلی ممنون از لطف شما.\n\nمعمولا کلاسها...   ham   
883  ﻿\n\n\n    دوست داری میلیونربشی؟\n\n\n>ازبین ک...  spam   
126  ﻿مرسی از این که به سوالم جواب دادین. ولی این ک...   ham   
434  ﻿راستی در تایید این مطلب باید عرض کنم من در یک...   ham   
270  ﻿ >> >>> >> >>> 2013/11/9 Faramarz Dehgan <far...   ham   
205  ﻿سلام.درست یکسال قبل یک دستگاه تلویزیون ویک دس...   ham   
921  ﻿   طراحی وب سایت استاندارد منطبق بر نیاز های ...  spam   
899  ﻿  سرگذشت مشهورترین میلیاردرهای جهان\n\n*آموزش...  spam   

                                             sentences  \
623   شامل 5000 كتاب الكترونيكي فارسي در زمينه هاي ...   
519      فیلترینگ بدن انسان *پد دفع سموم بدن کینوکی...   
404  سلام. خیلی ممنون از لطف شما. معمولا کلاسها دو ...   
883       دوست داری میلیونربشی؟ >ازبین کسانی که تا2...   
126  مرسی از این که به سوالم جواب دادین. ولی این که...   
434  راستی در تایید این مطلب باید عرض کنم من در یک ...   
270   >> >>> >> >>> 2013/11/9 Faramarz Dehgan <fara...   
205  سلام.درست یکسال قبل یک دستگاه تلویزیون ویک دست...   
921     طراحی وب سایت استاندارد منطبق بر نیاز های ش...   
899    سرگذشت مشهورترین میلیاردرهای جهان *آموزش فار...   

                                          cleaned_text  \
623  [شامل, ۵۰۰۰, کتاب, الکترونیکی, فارسی, در, زمین...   
519  [فیلترینگ, بدن, انسان, *پد, دفع, سموم, بدن, کی...   
404  [سلام, ., خیلی, ممنون, از, لطف, شما, ., معمولا...   
883  [دوست, داری, میلیونربشی, ؟, >ازبین, کسانی, که,...   
126  [مرسی, از, این‌که, به, سوالم, جواب, دادین, ., ...   
434  [راستی, در, تایید, این, مطلب, باید, عرض, کنم, ...   
270  [>>, >>>, >>, >>>, ۲۰۱۳, /, ۱۱, /, ۹, Faramarz...   
205  [سلام, ., درست, یکسال, قبل, یک, دستگاه, تلویزی...   
921  [طراحی, وب‌سایت, استاندارد, منطبق, بر, نیاز‌ها...   
899  [سرگذشت, مشهورترین, میلیاردرهای, جهان, *آموزش,...   

                                     pos_tagger_emails  \
623  [[(شامل, ADJ,EZ), (۵۰۰۰, NUM), (کتاب, NOUN,EZ)...   
519  [[(فیلترینگ, NOUN,EZ), (بدن, NOUN,EZ), (انسان,...   
404  [[(سلام, NOUN), (., PUNCT), (خیلی, ADV), (ممنو...   
883  [[(دوست, NOUN), (داری, VERB), (میلیونربشی, NOU...   
126  [[(مرسی, NOUN), (از, ADP), (این‌که, CCONJ), (ب...   
434  [[(راستی, ADV), (در, ADP), (تایید, NOUN,EZ), (...   
270  [[(>>, NOUN), (>>>, NOUN), (>>, NOUN), (>>>, N...   
205  [[(سلام, NOUN), (., PUNCT), (درست, ADJ,EZ), (ی...   
921  [[(طراحی, NOUN,EZ), (وب‌سایت, NOUN,EZ), (استان...   
899  [[(سرگذشت, NOUN,EZ), (مشهورترین, ADJ), (میلیار...   

                           candidates_extracted_emails  \
623  [<http, طریق, مبلغ, داستان, شعر, php, جلد کتاب...   
519  [مدت زمان, مشکلات, قدرت, فرد, هنگام خواب, تجرب...   
404  [اصرار, سه‌شنبه برگزار, گلفام, دوشنبه, درخواست...   
883  [جای نام, لامپهای LED, نگاه, داشتن دانه‌های, س...   
126  [مشکل, دکترا, بذاره ارشد, بره, لیسانس بره, است...   
434  [منطقه, نواحی ساحلی, مطلب, برنامه‌ی تلویزیونی,...   
270  [آمادگی, کلاهبرداریها, مایه, نفعتان, آقای, قیم...   
205  [یکسال, محصولات LG, دستگاه, باپست, محصولات, خر...   
921  [مدت زمان, -وب, تعداد, -- You, قابلیت ارسال, r...   
899  [تعداد, نجاتی, <http, com, خرید جهانگردان, مجل...   

                                   cos_sim_norm_emails  \
623  [[0.15838453], [0.4065104], [1.8756248], [0.71...   
519  [[-0.22426885], [0.7470231], [-0.6690502], [0....   
404  [[0.055834502], [0.9046209], [-1.0235187], [0....   
883  [[0.11021057], [-0.5266514], [-0.64906013], [1...   
126  [[0.87062573], [0.9131857], [1.9140059], [1.07...   
434  [[0.28595188], [-1.814342], [-0.16023916], [-1...   
270  [[1.0198004], [-0.44386572], [0.65757495], [0....   
205  [[0.15995783], [0.12644246], [1.4406176], [-0....   
921  [[-0.421883], [-0.13566166], [0.8050519], [0.8...   
899  [[0.7090529], [-0.16887182], [-0.8824328], [0....   

                                          10th_cos_sim  label_id  
623  [[3.1588254], [2.862668], [2.5528345], [2.2627...         1  
519  [[3.6166549

In [90]:
len(df_emails['10th_cos_sim'].iloc[0])

10

In [212]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

# Split dataset into features and target variable

# Split dataset into training set and test set
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=42)

In [214]:
for i in range(x.values.shape[0]):
    if(len(x.values[i])!=keyword_count):
        print(i, len(x.values[i]))
x.values

(1000,)

In [222]:
X=np.concatenate(x.values)
X=X.reshape(-1,keyword_count)
X.shape

(1000, 10)

In [223]:
x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)


In [225]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score

k_values = list(range(1, 21))
accuracy_scores = []

for k in k_values:
    knn_classifier = KNeighborsClassifier(n_neighbors=k)
    knn_classifier.fit(x_train, y_train)
    y_pred = knn_classifier.predict(x_test)
    accuracy = accuracy_score(y_test, y_pred)
    accuracy_scores.append(accuracy)

# Find the optimal value of K based on the highest accuracy
optimal_k = k_values[accuracy_scores.index(max(accuracy_scores))]

print("Optimal value of K:", optimal_k)
print("Accuracy:", max(accuracy_scores))

Optimal value of K: 12
Accuracy: 0.7466666666666667


In [226]:
from sklearn.model_selection import cross_val_score, KFold
import numpy as np

knn=KNeighborsClassifier(n_neighbors=optimal_k)
# Perform 10-fold cross-validation
kf = KFold(n_splits=10, shuffle=True, random_state=42)

# Define the scoring metrics
scoring = ['accuracy', 'precision', 'recall', 'f1']

# Store the scores for each metric
scores = {metric: cross_val_score(knn, xxx, y, cv=kf, scoring=metric) for metric in scoring}

# Compute average and standard deviation for each metric
avg_scores = {metric: np.mean(scores[metric]) for metric in scoring}
std_scores = {metric: np.std(scores[metric]) for metric in scoring}

# Print results
for metric in scoring:
    print("Average {}: {:.4f}".format(metric, avg_scores[metric]))
    print("{} Standard Deviation: {:.4f}".format(metric, std_scores[metric]))

Average accuracy: 0.7670
accuracy Standard Deviation: 0.0417
Average precision: 0.7653
precision Standard Deviation: 0.0613
Average recall: 0.7733
recall Standard Deviation: 0.0528
Average f1: 0.7674
f1 Standard Deviation: 0.0414


In [227]:
df_emails_v_2=df_emails.copy()

In [228]:
from hazm import Normalizer, word_tokenize, stopwords_list, Stemmer
normalizer = Normalizer()
stemmer = Stemmer()
def preprocess_text(text):
    # Normalize text
    text = normalizer.normalize(text)
    
    # Tokenize text
    tokens = word_tokenize(text)
    
    # Remove punctuation and stopwords, and perform stemming
    cleaned_tokens = [stemmer.stem(token) for token in tokens if token not in stopwords_list() and token.isalnum()]
    
    return cleaned_tokens

# Apply preprocessing to each email in the dataset
df_emails_v_2['cleaned_text'] = df_emails_v_2['sentences'].apply(preprocess_text)

In [229]:
X = df_emails_v_2['cleaned_text']
Y = df_emails_v_2['label_id']
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size=0.3, random_state=42)


In [231]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score

# Convert text data into numerical features using TF-IDF vectorization
tfidf_vectorizer = TfidfVectorizer(analyzer='word', tokenizer=lambda x: x, preprocessor=lambda x: x, token_pattern=None)
X_train_tfidf = tfidf_vectorizer.fit_transform(X)
X_train, X_test, Y_train, Y_test = train_test_split(X_train_tfidf, Y, test_size=0.3, random_state=42)


# Train KNN classifiers for different values of K
k_values = list(range(1, 21))
accuracy_scores = []

for k in k_values:
    knn_classifier = KNeighborsClassifier(n_neighbors=k)
    knn_classifier.fit(X_train, Y_train)
    Y_pred = knn_classifier.predict(X_test)
    accuracy = accuracy_score(Y_test, Y_pred)
    accuracy_scores.append(accuracy)

# Find the optimal value of K based on the highest accuracy
optimal_k = k_values[accuracy_scores.index(max(accuracy_scores))]

print("Optimal value of K:", optimal_k)
print("Accuracy:", max(accuracy_scores))

Optimal value of K: 6
Accuracy: 0.9766666666666667


In [232]:
from sklearn.model_selection import cross_val_score, KFold
import numpy as np

knn=KNeighborsClassifier(n_neighbors=optimal_k)
# Perform 10-fold cross-validation
kf = KFold(n_splits=10, shuffle=True, random_state=42)

# Define the scoring metrics
scoring = ['accuracy', 'precision', 'recall', 'f1']

# Store the scores for each metric
scores = {metric: cross_val_score(knn, X_train_tfidf, Y, cv=kf, scoring=metric) for metric in scoring}

# Compute average and standard deviation for each metric
avg_scores = {metric: np.mean(scores[metric]) for metric in scoring}
std_scores = {metric: np.std(scores[metric]) for metric in scoring}

# Print results
for metric in scoring:
    print("Average {}: {:.4f}".format(metric, avg_scores[metric]))
    print("{} Standard Deviation: {:.4f}".format(metric, std_scores[metric]))

Average accuracy: 0.9670
accuracy Standard Deviation: 0.0149
Average precision: 0.9728
precision Standard Deviation: 0.0279
Average recall: 0.9601
recall Standard Deviation: 0.0212
Average f1: 0.9660
f1 Standard Deviation: 0.0167
